In [1]:
import os, numpy as np, pandas as pd, cartopy.crs as ccrs, bokeh
import holoviews as hv, geoviews as gv

from colorcet import kbc
from holoviews.util import Dynamic

_ = hv.extension('bokeh', width=100, logo=False);

read data, sort them by area and add some text

In [2]:
df = pd.read_csv('./data/glaciers-explorer.csv')
df = df.sort_values(by='rgi_area_km2').reset_index(drop=True)
df['text'] = ['Id: {} - Area: {:.2f} km2 - Glaciers: {}'.format(i, a, n) 
              for i, (a, n) in enumerate(zip(df.rgi_area_km2, df.n_glaciers))]

In [3]:
df

cenlon  cenlat  rgi_area_km2  dem_mean_elev  dem_max_elev  dem_min_elev  \
0       61.5    65.5         0.010    1063.981323   1072.000000   1059.000000   
1       14.5    46.5         0.011    2596.733398   2644.000000   2553.000000   
2      -70.5   -33.5         0.012    2387.878906   2403.000000   2350.000000   
3       40.5    40.5         0.013    3257.309082   3295.000000   3230.000000   
4       15.5    46.5         0.015    2393.958252   2423.000000   2348.000000   
5      -73.5   -11.5         0.017    4576.683594   4627.000000   4517.000000   
6       19.5    43.5         0.019    2319.783447   2408.000000   2092.000000   
7     -120.5    40.5         0.020    2680.942383   2729.000000   2634.000000   
8       95.5    70.5         0.021     781.121399    798.000000    768.000000   
9      157.5    53.5         0.022    2428.964844   2446.000000   2392.000000   
10     117.5    58.5         0.024    1491.623779   1584.000000   1453.000000   
11     159.5    55.5         0.025    1397.125000   1430.000000   1382.000000   
12      86.5    49.5         0.026    2958.243896   2996.000000   2917.000000   
13    -175.5    67.5         0.028     573.559998    594.000000    554.000000   
14      92.5    49.5         0.029    1571.043701   1575.000000   1567.000000   
15     174.5    62.5         0.030     420.991638    477.000000    356.000000   
16      89.5    55.5         0.032    1586.628540   1615.000000   1548.000000   
17      14.5    42.5         0.033    2804.962158   2860.000000   2702.000000   
18     -70.5   -44.5         0.033    1793.104126   1830.000000   1764.000000   
19     105.5    76.5         0.036     486.468872    512.000000    457.000000   
20    -110.5    45.5         0.041    3195.564819   3312.500000   3105.500000   
21     -43.5    62.5         0.051    2093.314941   2166.000000   1995.000000   
22      35.5    39.5         0.056    3564.817139   3779.000000   3438.000000   
23     -54.5    71.5         0.058     513.369873    564.000000    454.000000   
24      73.5    43.5         0.060    3904.114258   3958.000000   3805.000000   
25      85.5    50.5         0.061    2336.126465   2414.000000   2294.500000   
26     -77.5    71.5         0.062     770.461548    778.000000    759.000000   
27      60.5    64.5         0.064     714.981628    780.000000    678.000000   
28     -67.5   -25.5         0.064    5217.793945   5282.000000   5175.000000   
29     157.5    52.5         0.065    1707.732178   1784.000000   1667.000000   
...      ...     ...           ...            ...           ...           ...   
1733   -76.5    80.5      2639.826     913.504076   1322.800000    368.950000   
1734  -133.5    59.5      2643.064    1602.156889   1856.103044   1339.925059   
1735   -75.5    82.5      2697.103    1251.751121   1554.868421    808.736842   
1736   -77.5    78.5      2723.372     603.109009   1087.700000     62.100000   
1737   -24.5    70.5      2727.302    1150.127837   1366.505495    909.851648   
1738    80.5    42.5      2781.911    4252.872601   4590.864623   3925.094508   
1739   -79.5    77.5      2826.876     615.966299   1001.125000    163.975000   
1740   -51.5    66.5      2859.346    1123.426343   1417.987952    699.566265   
1741   -82.5    75.5      2935.989    1187.776489   1825.000000      0.000000   
1742    75.5    36.5      2960.712    5102.947430   5493.257905   4690.701581   
1743  -138.5    60.5      3031.389    1177.918647   1395.347222    962.050926   
1744   -80.5    78.5      3083.660     959.973648   1632.500000     66.000000   
1745    18.5    79.5      3089.505     603.045229    916.571429    208.238095   
1746   -27.5    70.5      3127.441    1556.240278   1866.240602    947.812030   
1747   -72.5   -48.5      3170.940    1554.955773   1804.427711   1306.052209   
1748   -73.5   -48.5      3172.966    1068.938587   1298.731429    808.154286   
1749   -65.5    67.5      3248.296    1293.067357   1491.491525    998.790960   
1750    77.5    35.5      3338.110   

convert into a holoviews dataset with key dimensions 'cenlon' and 'canlat' and some value dimensions

In [4]:
data = hv.Dataset(df, [('cenlon', 'Longitude'), ('cenlat', 'Latitude')],
                     [('tstar_avg_prcp', 'Annual Precipitation (mm/yr)'),
                      ('rgi_area_km2', 'Area'), ('text', 'Info'),
                      ('tstar_avg_temp_mean_elev', 'Annual Temperature at avg. altitude'), 
                      ('dem_mean_elev', 'Elevation'), 'n_glaciers'])

specifie some options for the upcoming holoviews objects

In [5]:
temp_kw   = dict(num_bins=50, adjoin=False, normed=False, bin_range=data.range('tstar_avg_temp_mean_elev'))
prcp_kw   = dict(num_bins=50, adjoin=False, normed=False, bin_range=data.range('tstar_avg_prcp'))

geo_opts  = dict(width=600, height=300, cmap=kbc[::-1][20:], global_extent=True, logz=False, colorbar=True, 
                 projection=ccrs.Robinson(), color_index='rgi_area_km2', default_tools=[], toolbar=None, alpha=1.0)
elev_opts = dict(width=600, height=300, show_grid=True, color='#7d3c98', default_tools=[], toolbar=None, alpha=1.0)
temp_opts = dict(width=600, height=300,            fill_color='#f1948a', default_tools=[], toolbar=None, alpha=1.0)
prcp_opts = dict(width=600, height=300,            fill_color='#85c1e9', default_tools=[], toolbar=None, alpha=1.0)

# create the background 'worldmap'
geo_bg    = gv.feature.coastline.options(default_tools=['wheel_zoom'], toolbar=None)

In [ ]:
# (geo_bg * gv.Points(data).options(**geo_opts) +
#  data.to(hv.Scatter, 'dem_mean_elev','cenlat',[]).options(**elev_opts) + 
#  data.hist('tstar_avg_temp_mean_elev', **temp_kw).options(**temp_opts) +
#  data.hist('tstar_avg_prcp',           **prcp_kw).options(**prcp_opts)).options(shared_axes=False).cols(2)

create functions for each subplot with the selected data, could be called with a subset of the data

In [6]:
def geo(data):   return gv.Points(data).options(**geo_opts)
def elev(data):  return data.to(hv.Scatter, 'dem_mean_elev', 'cenlat', []).options(**elev_opts)
def temp(data):  return data.hist('tstar_avg_temp_mean_elev', **temp_kw).options(**temp_opts)
def prcp(data):  return data.hist('tstar_avg_prcp',           **prcp_kw).options(**prcp_opts)

def count(data): return hv.Div('<p style="font-size:20px">Glaciers selected: ' + 
                        str(data.dframe().n_glaciers.sum()) + "</font>").options(height=40)

create a HoverTool with some text (field 'text'), create holoview objects with all the data, which will always be displayed in the background

In [7]:
from bokeh.models import HoverTool
hover = HoverTool(tooltips=[('Info', '@{text}')])

static_geo  = geo( data).options(alpha=0.03, tools=[hover, 'box_select'])
static_elev = elev(data).options(alpha=0.1,  tools=[       'box_select'])
static_temp = temp(data).options(alpha=0.1)
static_prcp = prcp(data).options(alpha=0.1)

function for subset selection, look at all selections in each subplot and put it together to get one selection

In [8]:
def combine_selections(**kwargs):
    "Combines selections on all available plots into a single selection by index."
    
    # if all selections are empty return slice(None) = is a slice instance with the default values (= all values)
    if all(not v for v in kwargs.values()):
        return slice(None)
    selection = {}
    # loop through all selections of the different subplots
    for key, bounds in kwargs.items():
        # if selection has no bounds do nothing with the selection
        if bounds is None:
            continue
        # if there are two bounds (this means for example in the histogram selection along the x axis, bound_xsmall to bound_xlarge) 
        # save them in the selection dictionary with the key is the subplot
        elif len(bounds) == 2:
            selection[key] = bounds
        # if selection is a rectangular you have four points, so first split the key (look like xboundname__yboundname) and 
        # then save the four selection points (tuple of the left, bottom, right and top coordinates)
        else:
            xbound, ybound = key.split('__')
            selection[xbound] = bounds[0], bounds[2]
            selection[ybound] = bounds[1], bounds[3]
    return sorted(set(data.select(**selection).data.index))

# if some selections call function combine_selections and return selected data otherwise return all the data
def select_data(**kwargs):
    return data.iloc[combine_selections(**kwargs)] if kwargs else data

create streams for the selection on each subplot, BoundsXY for geographical and BoundsX for histogramms, and put all together in selections

In [9]:
from holoviews.streams import Stream, BoundsXY, BoundsX

geo_bounds  = BoundsXY(source=static_geo,  rename={'bounds':  'cenlon__cenlat'})
elev_bounds = BoundsXY(source=static_elev, rename={'bounds':  'dem_mean_elev__cenlat'})
temp_bounds = BoundsX( source=static_temp, rename={'boundsx': 'tstar_avg_temp_mean_elev'})
prcp_bounds = BoundsX( source=static_prcp, rename={'boundsx': 'tstar_avg_prcp'})

selections  = [geo_bounds, elev_bounds, temp_bounds, prcp_bounds]

In [10]:
# create DynamicMap which calling the function select_data whenever there is some change in one of the selections (_bounds), so 
# you than have the selected data in dyn_data
dyn_data  = hv.DynamicMap(select_data, streams=selections)

# Dynamic calling the function given with operation only with the selected data ('dyn_data') whenever there is a change in 'dyn_data', 
# give back a Holoviews Div object
dyn_count = Dynamic(dyn_data, operation=count)

# creating holoviews overlays with the background, the static plots and on top the selected plots, whenever there is a change in 'dyn_data'
geomap  = geo_bg * static_geo  * Dynamic(dyn_data, operation=geo)
elevation        = static_elev * Dynamic(dyn_data, operation=elev)
temperature      = static_temp * Dynamic(dyn_data, operation=temp)
precipitation    = static_prcp * Dynamic(dyn_data, operation=prcp)

In [11]:
# function for clearing all selections and force a 'change' with trigger so 'Dynamic' is doing its thing (dynamically)
def clear_selections(arg=None):
    geo_bounds.update(bounds=None)
    elev_bounds.update(bounds=None)
    temp_bounds.update(boundsx=None)
    prcp_bounds.update(boundsx=None)
    Stream.trigger(selections)

In [14]:
# creating a button which is calling the clear_selections function whenever there is a click on it
import panel as pn
pn.extension()

clear_button = pn.widgets.Button(name='Clear selection')
clear_button.param.watch(clear_selections, 'clicks');

In [13]:
# make some html designing things
title       = '<p style="font-size:35px">World glaciers explorer</p>'
instruction = 'Box-select on each plot to subselect; clear selection to reset.<br>' + \
              'See the <a href="https://anaconda.org/jbednar/glaciers">Jupyter notebook</a> source code for how to build apps like this!'
oggm_logo   = '<a href="https://github.com/OGGM/OGGM-Dash"><img src="https://raw.githubusercontent.com/OGGM/oggm/master/docs/_static/logos/oggm_s_alpha.png" width=170></a>'
pv_logo     = '<a href="https://pyviz.org"><img src="http://pyviz.org/assets/PyViz_logo_wm.png" width=80></a>'

In [17]:
# using panel (pn) to arrange the different html elements
header = pn.Row(pn.Pane(oggm_logo, width=170), pn.Spacer(width=50), 
                pn.Column(pn.Pane(title, height=25, width=400), pn.Spacer(height=15), pn.Pane(instruction, width=500)),
                pn.Spacer(width=180), pn.Column(pn.Pane(dyn_count), clear_button, pn.Spacer(height=15)), 
                pn.Pane(pv_logo, width=80))

pn.Column(header, pn.Spacer(height=40), pn.Row(geomap, elevation), pn.Row(temperature, precipitation))

Column
    [0] Row
        [0] Markdown(str, width=170)
        [1] Spacer(width=50)
        [2] Column
            [0] Markdown(str, height=25, sizing_mode='fixed', width=400)
            [1] Spacer(height=15)
            [2] Markdown(str, width=500)
        [3] Spacer(width=180)
        [4] Column
            [0] HoloViews(DynamicMap)
            [1] Button(name='Clear selection')
            [2] Spacer(height=15)
        [5] Markdown(str, width=80)
    [1] Spacer(height=40)
    [2] Row
        [0] HoloViews(DynamicMap)
        [1] HoloViews(DynamicMap)
    [3] Row
        [0] HoloViews(DynamicMap)
        [1] HoloViews(DynamicMap)